# Overview

This notebook allows you to try and choose different subsets of input variables for the [COMPAS dataset](http://www-student.cse.buffalo.edu/~atri/ml-and-soc/support/notebooks/datasets/cox-violent-parsed_filt.csv) to try and change the final predictive accuracy of a linear model.

# Acknowledgement

The code in this notebook was originally created by [Sanchit Batra](https://www.linkedin.com/in/sanchitbatra/). 

The [COMPAS dataset](http://www-student.cse.buffalo.edu/~atri/ml-and-soc/support/notebooks/datasets/cox-violent-parsed_filt.csv) generated by [ProPublica](https://github.com/propublica/compas-analysis). This specific version is taken from [Kaggle](https://www.kaggle.com/danofer/compass#cox-violent-parsed_filt.csv), which in turn got the original data from [ProPublica](https://github.com/propublica/compas-analysis).

## First Step

This part loads the [COMPAS dataset](http://www-student.cse.buffalo.edu/~atri/ml-and-soc/support/notebooks/datasets/cox-violent-parsed_filt.csv), displays it and chooses the target variable and decides on the train vs. test split.

You do not have to do anything other than click the Run button.

In [14]:
#@title First Step { display-mode: "form" }
import pandas as pd
import ipywidgets as widgets

#Load the CSV file
dataset = pd.read_csv('http://www-student.cse.buffalo.edu/~atri/algo-and-society/support/notebooks/datasets/cox-violent-parsed_filt.csv')

#display the CSV file
display(dataset)

from sklearn.preprocessing import LabelEncoder
import numpy as np


"""
Clean up the dataset.
Currently ONLY works for COMPAS
"""

def clean_dataset(df: pd.DataFrame):

  le = LabelEncoder()

  # Filter rows with values outside of range
  df = df[df['is_recid'] != -1]
  df = df[df['decile_score.1'] != -1]
  df = df[df['decile_score'] != -1]


  #Re-name the recidivism variable
  df['recidivism_within_2_years'] = df['is_recid']
  #print("After 4th change========")
  #display(df)
    
  # Categorize variables
    
  le.fit(df['race'])
  df['race'] = le.transform(df['race'])
    
  le.fit(df['age_cat'])
  df['age_cat'] = le.transform(df['age_cat'])
    
  le.fit(df['v_score_text'])
  df['v_score_text'] = le.transform(df['v_score_text'])
    
  df['score_text'] = np.where(df['score_text'] == 'Low', 0, 1)
    
  df["sex"] = np.where(df["sex"] == "Male", 0, 1)

  return df

#Clean the dataset

dataset = clean_dataset(dataset)

#display(dataset)

test_split_frac = float(0.2)

print("Choosing the test set to be "+str(test_split_frac*100)+"% of the dataset")
#@title Split the dataset into training and testing sets { display-mode: "form" }
from sklearn.model_selection import train_test_split

#split the dataset into training/testing (currently test set is 20% of the dataset)
training_set, test_set = train_test_split(dataset, test_size=test_split_frac)

#display(training_set)
#display(test_set)
#@title Choose target variable { display-mode: "form" }

columns = [
    "sex", 
    "race",
    "age",
    "age_cat",
    "score_text",
    "priors_count.1", 
    "priors_count", 
    "juv_fel_count", 
    "juv_misd_count", 
    "juv_other_count", 
    "is_violent_recid",
    "decile_score.1",
    "v_decile_score",
    "v_score_text",
#    "recidivism_within_2_years"
]

"""
Choose the column being predicted (i.e. target variable)
"""

#@title Check your choice { display-mode: "form" }
target_var = 'recidivism_within_2_years'

print("The target variable:  "+target_var)

id                   name  ... priors_count.1 event
0      1.0       miguel hernandez  ...              0     0
1      2.0       miguel hernandez  ...              0     0
2      3.0           michael ryan  ...              0     0
3      4.0            kevon dixon  ...              0     1
4      5.0               ed philo  ...              4     0
...    ...                    ...  ...            ...   ...
18311  NaN  alexsandra beauchamps  ...              5     0
18312  NaN        winston gregory  ...              0     0
18313  NaN            farrah jean  ...              3     0
18314  NaN    florencia sanmartin  ...              2     0
18315  NaN    florencia sanmartin  ...              2     0

[18316 rows x 40 columns]

Choosing the test set to be 20.0% of the dataset
The target variable:  recidivism_within_2_years


## Second Step

This is the step where you pick the input variables. This is the only part of the notebook where you will be doing anything nontrivial.

Hit run and then choose the subset of the input variables that you want to pick. 

In [15]:
#@title Choose your input variables { display-mode: "form" }

input_choice=widgets.SelectMultiple(
    options=columns,
    value=['race','age'],
    #rows=10,
    description='Input Variable(s)',
    disabled=False
)

display(input_choice)

SelectMultiple(description='Input Variable(s)', index=(1, 2), options=('sex', 'race', 'age', 'age_cat', 'score…

## Final Step

Just click the Run button for the rest of the ML pipeline to run. Check out the accuracy number printed at the very end. Note that if you change the subset of input variables picked in the above window do NOT click the Run in the previous code block. Just clicking the Run button on the code block below is enough.

In [17]:
#@title Run the rest of the ML pipeline { display-mode: "form" }
input_columns= list(input_choice.value)

if target_var in input_columns:
  print("The target variable is part of the input variables. DO NOT PROCEED!!!")
else:
  print("You chose the following input variables:  "+str(input_columns))
#@title Create the final training and testing sets { display-mode: "form" }
#Get the training input values and labels
train_inputs = training_set[input_columns].to_numpy()
train_labels = training_set[target_var].to_numpy()

#display(train_input)
#display(train_label)

#Get the testing input values and labels
test_inputs = test_set[input_columns].to_numpy()
test_labels = test_set[target_var].to_numpy()


model_class = 'Linear Classifier'

print("Using the following model class: "+model_class)
#@title Finish it off! { display-mode: "form" }
# Import stuff for linear classifier
from sklearn.linear_model import SGDClassifier
LinearClassifier = SGDClassifier

# Import stuff for decision trees
from sklearn import tree

# Import stuff for NNs
from sklearn.neural_network import MLPClassifier

# Import stuff for accuracy
from sklearn.metrics import accuracy_score

###################################################################################################################
# NOTE TO STUDENTS: Start reading from here
###################################################################################################################
try:
    if model_class == 'Linear Classifier':
      model = LinearClassifier()
    elif model_class == 'Decision Tree':
      model = tree.DecisionTreeClassifier()
    elif model_class == 'Neural Networks':
      #model = MLPClassifier(solver='lbfgs', alpha=1e-5,hidden_layer_sizes=(5, 2), random_state=1)
      model = MLPClassifier(random_state=1, max_iter=1000)

    # Train the model using the label column selected on the training dataset without the label column
    model.fit(train_inputs, train_labels)
    
    # Predict labels using the testing dataset without the label column
    predictions = model.predict(test_inputs)
    
    # Use the number of mismatched labels as a measure of the accuracy for the classification task
    score = accuracy_score(test_labels, predictions)
    
    print("Accuracy score: {}%".format(str(round(score*100, 2))))
    
except ValueError as e:
    print(e)

You chose the following input variables:  ['sex', 'race', 'age', 'priors_count.1', 'priors_count', 'juv_fel_count', 'juv_misd_count', 'juv_other_count', 'is_violent_recid']
Using the following model class: Linear Classifier
Accuracy score: 56.84%
